# Using rapidfuzz to extract affiliatuons from RES

First the JSON output file from tezseract is read in and made into a useable dataframe

In [75]:
#Importing the libraries
import json
import pandas as pd
from rapidfuzz import process
import requests

# Load input files from github
#tesseract_input = requests.get('https://raw.githubusercontent.com/Matt970204/Affiliations_V2/main/1_Input%20files%20and%20processing%20input%20files/1_1_Input%20files/Tesseract%20affiliation%20output/AER/AER_aff_output_1971_2010.json')
#json_data = tesseract_input.json()

# Import JSON file
f = open('/Users/MattJohnson/Desktop/Affiliations/1_Input files and processing input files/1_1_Input files/Tesseract affiliation output/QJE/QJE_aff_ref_output_1977_2010.json')
json_data = json.load(f)

# Define Journal and Dataframe
Journal_Name = 'QJE'
Reference_Data_List = []

# Extract Json Data into dataframe
for key1, value1 in json_data.items():
    Article_ID = key1
    content_type = value1["content_type"]
    author_list = value1["authors"]
    authorsNo = len(author_list)
    stable_url = value1["stable_url"]
    ref_string_found = ''
    ref_string_raw = ''
    list = []
    for key2 in value1["affiliations"]:
        #print(key2)
        if key2 == "found":
            Ref_type = key2
            ref_string_found = value1["affiliations"][key2]
            #print("found")
        else: 
            for key3 in value1["affiliations"]["raw"]:
                    list.append(key3)
                    Ref_type = key2
                    #print(key1, "   ",len(value1["affiliations"]["raw"]))
                    #print("raw", key3)
                    #ref_string_raw = value1["affiliations"][key2][key3]
                    #print(ref_string)
            print(list)
            #print(list[-1])
            if len(list) >0:
                raw = value1["affiliations"][key2][list[-1]]
                print(raw)
                print(type(raw))
                reverse = raw[::-1]
                print(reverse)
                ref_string_raw = "".join(reverse)

        
    for key2 in value1["affiliations"]:
        #print(key2)
        if key2 == "found":
            Ref_type = key2
            break
        else: 
            Ref_type = key2

    Reference_Data_List.append({'Journal_Name' : Journal_Name,
    'Authors_count' : authorsNo, 
    'Authors_list' : author_list,
    'Article_ID' : Article_ID, 'content_type' : content_type,
    'stable_url' : stable_url, 
    'Ref_type': Ref_type,  
    'ref_string_found':ref_string_found,
     'ref_string_raw': ref_string_raw})


QJE_aff_ref_output_1940_2010 = pd.DataFrame.from_records(Reference_Data_List)     
QJE_aff_ref_output_1940_2010.to_excel('/Users/MattJohnson/Desktop/Affiliations/2_Extracting affilitations/3_Consolidation/QJE/QJE_aff_ref_output_1940_2010_Initial.xlsx')        

['35', '34']
['This content downloaded from\n197.185.109.154 on Fri, 29 Apr 2022 05:37:39 UTC\nAII use subject to https://about.jstor.org/terms\n', 'REFERENCES\n\nBarberis, Nicholas, Andrei Shleifer, and Robert Vishny, *A Model of Investor Sen-\ntiment," Journal of Financial Economics, 49 (1998), 307—343.\n\nCascells, Ward, Arno Schoenberger, and Thomas Graboys, *Interpretations of\nPhysicians of Clinical Laboratory Results," New England Journal of Medicine,\n299 (1978), 999-1001.\n\nCutler, David, and Richard Zeckhauser, *Extending the Theory to Meet the Prac-\ntice of Insurance," in Brookings-Wharton Papers on Financial Services, Robert\nLitan and Richard Herring, eds. (Washington, DC: Brookings Institution,\n2004).\n\nFischhoff, Baruch, Paul Slovic, and Sarah Lichtenstein, *Fault Trees: Sensitivity of\nAssessed Failure Probabilities to Problem Representation," Journal of Exper-\nimental Psychology: Human Perceptions and Performance, 4 (1978), 330—344.\n\nGriffin, Dale, and Amos Tver

Next the Unique list of universities is read in, this is used as a database to check the affiliton string against using rapidfuzz. 

In [76]:
# Load in the list of unique Universites from github stored in 2_fuzzy matching
#affs = pd.read_excel("https://raw.githubusercontent.com/Matt970204/Affiliations_V2/main/2_Extracting%20affilitations/2_Fuzzy%20matching/University%20list/Unique%20Universities.xlsx")


affs = pd.read_excel('/Users/MattJohnson/Desktop/Affiliations/2_Extracting affilitations/2_Fuzzy matching/University list/Unique Universities.xlsx')


for i in range(len(affs)):
    #Replaceing title case and stripping leading space
    #affs.iat[i,0] = affs.iat[i,0].strip().title()
    affs.iloc[i]['Affilliation'] = affs.iloc[i]['Affilliation'].strip().title()
    #affs.iat[i,0] = affs.iat[i,0].strip().upper()

Affiliation_choices = affs['Affilliation'].values.tolist()
#print(Affiliation_choices.shape)

print(affs['Affilliation'].head())

/var/folders/23/ft9qf9c11rj_vqhbjml910f40000gn/T/ipykernel_61230/1194697991.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  affs.iloc[i]['Affilliation'] = affs.iloc[i]['Affilliation'].strip().title()


0      Yale University
1            Cambridge
2              Harvard
3               Oxford
4    Oxford University
Name: Affilliation, dtype: object


In [77]:
#testdata = RES_1940_2010.loc[0:20].reset_index(drop = True)
testdata = QJE_aff_ref_output_1940_2010

for i in range(len(testdata)):
        testdata.loc[i,['ref_string_found_clean']] = testdata.iloc[i]['ref_string_found'].strip().title()
        testdata.loc[i,['ref_string_raw_clean']] = testdata.iloc[i]['ref_string_raw'].strip().title()

print(testdata.columns.values)

['Journal_Name' 'Authors_count' 'Authors_list' 'Article_ID' 'content_type'
 'stable_url' 'Ref_type' 'ref_string_found' 'ref_string_raw'
 'ref_string_found_clean' 'ref_string_raw_clean']


In [78]:
#Reading in the master file and correctly formatting the article ID to match back onto the meltef file

#Load in master from Github
#AER_master = pd.read_excel("https://raw.githubusercontent.com/Matt970204/Affiliations_V2/main/1_Input%20files%20and%20processing%20input%20files/1_1_Input%20files/Master%20lists/Processed/AER_processed.xlsx")

#Local store of AER_master
QJE_master = pd.read_excel('/Users/MattJohnson/Desktop/Affiliations/1_Input files and processing input files/1_1_Input files/Master lists/Processed/QJE_processed.xlsx')
for i in range(len(QJE_master)):
    QJE_master.loc[i,['Article_ID']] = QJE_master.loc[i,['stable_url']].to_string().rsplit('/',1)[-1]

QJE_master_condenced  = QJE_master[['Article_ID','year']]
QJE_master_condenced['year'] = QJE_master_condenced['year'].astype('int')
QJE_master_condenced.head()

/var/folders/23/ft9qf9c11rj_vqhbjml910f40000gn/T/ipykernel_61230/567971768.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  QJE_master_condenced['year'] = QJE_master_condenced['year'].astype('int')


Article_ID  year
0   26372672  2016
1   26372673  2016
2   26372674  2016
3   26372675  2016
4   26372676  2016

In [79]:
# Merging the masterfile onto the new melted file to get additional data
testdata_merged = testdata.merge(QJE_master_condenced, how = 'left', on = 'Article_ID')
testdata_merged = testdata_merged.sort_values(by=['year'])
testdata = testdata_merged.reset_index(drop = True)

In [80]:
# Excel output to get an overview of the data
testdata.head
testdata.to_excel('/Users/MattJohnson/Desktop/Affiliations/2_Extracting affilitations/3_consolidation/QJE/QJE_aff_ref_output_1940_2010_affs_out setup.xlsx') 

In [81]:
testdata2 = testdata

In [82]:
import re
from rapidfuzz import fuzz
import math

for x in range(len(testdata2)):
    str1 = testdata2.iloc[x]['ref_string_found_clean']

#Splitting up the string into authors lines
    ref_split = re.split(r"\n",str1)
    #Removing blank lines from the split
    while("" in ref_split):
        ref_split.remove("")

    author_count = 0
    for j in range(len(ref_split)):
        for z in Affiliation_choices:
            ratio  = fuzz.partial_ratio(ref_split[j], z)
            if ratio > 95:
                testdata2.loc[x, str(author_count)+'_author_affs'] = ref_split[j]
                print(testdata2.loc[x, str(author_count)+'_author_affs'])
                author_count = author_count+1
                break
    print(x)

    

0
1
2
Bell Laboratories
3
4
5
6
7
Harvard University
8
York University
9
10
11
12
Columbia University
13
14
Àarhus Universitet, Denmark, And University Of Essex, United
15
16
Harvard University
California Institute Of Technology
University Of Arizona
17
Churchill College, Cambridge
18
19
20
Massachusetts Institute Of Technology
21
22
23
24
25
26
Board Of Governors Of The Federal, Reserve System
University Of Massachusetts, Boston
27
28
29
30
31
32
33
Board Of Governors Of The Federal Reserve System
34
Federal Reserve Bank Of San Francisco
35
Harvard University
Stanford University
36
37
School For Advanced Studies In The Social Sciences, And Cepremap,
Paris
38
39
40
University Of Virginia
Australian National University
41
42
43
State University Of New York At Albany
44
45
The Hebrew University
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
€1978 By The President And Fellows Of Harvard College. Published By John Wiley & Sons, Inc.
71
72
73
74
75
76
77
78
79
80

In [83]:
testdata = testdata2[['Journal_Name' ,'Authors_count', 'Authors_list', 'Article_ID', 'content_type',
 'stable_url', 'Ref_type', 'year',
 'ref_string_found' ,
 'ref_string_found_clean',
 'ref_string_raw',
 'ref_string_found_clean' ,
 'ref_string_raw_clean' ,
 '0_author_affs', 
 '1_author_affs',
 '2_author_affs',
 '3_author_affs',
 '4_author_affs' ]]

In [84]:
# Excel output to get an overview of the data
testdata.head
testdata.to_excel('/Users/MattJohnson/Desktop/Affiliations/2_Extracting affilitations/3_consolidation/QJE/QJE_aff_ref_output_1940_2010_affs_out test.xlsx') 

In [85]:
print(testdata.columns.values)

['Journal_Name' 'Authors_count' 'Authors_list' 'Article_ID' 'content_type'
 'stable_url' 'Ref_type' 'year' 'ref_string_found'
 'ref_string_found_clean' 'ref_string_raw' 'ref_string_found_clean'
 'ref_string_raw_clean' '0_author_affs' '1_author_affs' '2_author_affs'
 '3_author_affs' '4_author_affs']


In [86]:
# Creating a dictionary for consolidation
# Read in from Excel sheet, 2 columns first one with incorrect spelling and second one with correct spellig

misspellings = pd.read_excel('/Users/MattJohnson/Desktop/Affiliations/2_Extracting affilitations/2_Fuzzy matching/University list/consolidated list.xlsx', 'Misspellings')
misspellings = misspellings[['Incorrect spelling', 'Correct spelling']]

cities = pd.read_excel('/Users/MattJohnson/Desktop/Affiliations/2_Extracting affilitations/2_Fuzzy matching/University list/consolidated list.xlsx', 'Cities')

comma_in_name = pd.read_excel('/Users/MattJohnson/Desktop/Affiliations/2_Extracting affilitations/2_Fuzzy matching/University list/consolidated list.xlsx', 'Comma in name')

colleges_full = pd.read_excel('/Users/MattJohnson/Desktop/Affiliations/2_Extracting affilitations/2_Fuzzy matching/University list/consolidated list.xlsx', 'Colleges Full')
colleges_full = colleges_full[['Incorrect spelling', 'Correct spelling']]

colleges = pd.read_excel('/Users/MattJohnson/Desktop/Affiliations/2_Extracting affilitations/2_Fuzzy matching/University list/consolidated list.xlsx', 'Colleges')
correct = pd.read_excel('/Users/MattJohnson/Desktop/Affiliations/2_Extracting affilitations/2_Fuzzy matching/University list/consolidated list.xlsx', 'Correct')

frames = [misspellings, cities, comma_in_name,colleges_full ,colleges,correct]
consolidated_affiliations = pd.concat(frames)
print(consolidated_affiliations.shape)

for i in range(len(consolidated_affiliations)):
    #Replaceing title case and stripping leading space
    #affs.iat[i,0] = affs.iat[i,0].strip().title()
    consolidated_affiliations.iloc[i]['Incorrect spelling'] = consolidated_affiliations.iloc[i]['Incorrect spelling'].strip().title()
    #affs.iat[i,0] = affs.iat[i,0].strip().upper()

consolidated_affiliations_dict = consolidated_affiliations.set_index('Incorrect spelling').to_dict()['Correct spelling']
print(consolidated_affiliations_dict)

(1137, 2)
{'Bell Laboratories, Inc': 'Bell Laboratories', 'Board Of Governors Of The Federal Reseree System': 'Board Of Governors Of The Federal Reserve System', 'Board Of Governors Of The Federal Reseroe System': 'Board Of Governors Of The Federal Reserve System', 'Board Of Governors, Federal Reserve System': 'Board Of Governors Of The Federal Reserve System', 'Boston Unxversity': 'Boston University', 'Broum University': 'Brown University', 'California State University, Long Beach': 'California State University At Long Beach', 'California State University, Northridge': 'California State University At Northridge', 'California State Unizersity, Fullerton': 'California State University At Fullerton', 'Cambridge University': 'University of Cambridge', 'Carnegie Mellon University': 'Carnegie Mellon University', 'Carnegie- Mellon University': 'Carnegie-Mellon University', 'Carnegie- Mellon Unizersity': 'Carnegie-Mellon University', 'Cornell Unisersity': 'Cornell University', 'Department Of 

In [87]:
import numpy as np
testdata = testdata.replace(np.nan, '', regex=True)
testdata["0_author_affs_consolidated"] = ""
testdata["1_author_affs_consolidated"] = ""
testdata["2_author_affs_consolidated"] = ""
testdata["3_author_affs_consolidated"] = ""
testdata["4_author_affs_consolidated"] = ""
testdata["5_author_affs_consolidated"] = ""
testdata["4_author_affs"] = ""
testdata["5_author_affs"] = ""

for i in range(len(testdata)):
#for i in range(0,50):
#for i in range(2113,2114):
    authors = testdata.iloc[i]['Authors_list']
    for auth_no in range(len(authors)):
        #print(testdata.iloc[i]['0_author_affs'])
        testdata.loc[i,str(auth_no)+'_author_affs'] =  re.sub(r'\.','',testdata.iloc[i][str(auth_no)+'_author_affs'])
        testdata.loc[i,str(auth_no)+'_author_affs'] =  re.sub(r'The ','',testdata.iloc[i][str(auth_no)+'_author_affs'])
        #print(testdata.iloc[i]['0_author_affs'])
        list = []

    #Loop through the list of incorrect spellings and replace with corrected spellings
        for key in consolidated_affiliations_dict.keys():
            #testdata.loc[i,'0_author_affs_consolidated']  = testdata.iloc[i]['0_author_affs'].replace(key, consolidated_affiliations_dict[key])
            if key in testdata.iloc[i][str(auth_no)+'_author_affs']:
                list.append(key)
                #print(len(list))
                #print((key))
                #print(consolidated_affiliations_dict[key])

    #If there is more than 1 match in the consolidation it needs to match on the longer one, solves for college issue
                if len(list) <= 1:
                    testdata.loc[i,str(auth_no)+'_author_affs_consolidated']  = re.sub(key, consolidated_affiliations_dict[key],testdata.iloc[i][str(auth_no)+'_author_affs']).strip().rstrip(',')
                else:
                    #print(consolidated_affiliations_dict[list[0]])
                    #print(consolidated_affiliations_dict[list[1]])
                    if(len(consolidated_affiliations_dict[list[0]]) == len(consolidated_affiliations_dict[list[1]])):
                        #print("HERE")
                        if len(list[0]) > len(list[1]):
                            #print("HERE")
                            testdata.loc[i,str(auth_no)+'_author_affs_consolidated']  = re.sub(list[0], consolidated_affiliations_dict[list[0]],testdata.iloc[i][str(auth_no)+'_author_affs']).strip().rstrip(',')
                            #print(list[0])
                        else:
                            #print("this")
                            first_fix = re.sub(list[1], consolidated_affiliations_dict[list[1]],testdata.iloc[i][str(auth_no)+'_author_affs']).strip().rstrip(',') 
                            testdata.loc[i,str(auth_no)+'_author_affs_consolidated']  = re.sub(key, consolidated_affiliations_dict[key],first_fix).strip().rstrip(',') 
                    else:
                        #print("else")
                        #print(key)
                        first_fix = re.sub(list[0], consolidated_affiliations_dict[list[0]],testdata.iloc[i][str(auth_no)+'_author_affs']).strip().rstrip(',') 
                        #print(first_fix)
                        testdata.loc[i,str(auth_no)+'_author_affs_consolidated']  = re.sub(key, consolidated_affiliations_dict[key],first_fix).strip().rstrip(',') 
            # print(i)

                #print(re.sub(key, consolidated_affiliations_dict[key],testdata.iloc[i]['0_author_affs']))
            #else:
            #    testdata.loc[i,'0_author_affs_consolidated'] = ''
                #print(testdata.iloc[i]['0_author_affs_consolidated'])
        #testdata.loc[i,['1_author_affs']] =  re.sub(r'\.','',testdata.iloc[i]['1_author_affs'])
        #testdata.loc[i,['2_author_affs']] =  re.sub(r'\.','',testdata.iloc[i]['2_author_affs'])
        #if(testdata.iloc[i][str(auth_no)+'_author_affs_consolidated']):
        #    print("exists")
        print(i)
        print('Full ',testdata.loc[i,str(auth_no)+'_author_affs_consolidated'])
        #else: 
        #    print("non existant")
        auths_affs_split_And = re.split(' And ', testdata.iloc[i][str(auth_no)+'_author_affs_consolidated'])
        #print(auths_affs_split_And)
        #print(len(auths_affs_split_And))

        for aff in range(len(auths_affs_split_And)):
            testdata.loc[i,str(auth_no)+'_author_affs_consolidated_'+str(aff)]  = auths_affs_split_And[aff].strip().rstrip(',') 
            print('Auth', str(auth_no), str(aff) , testdata.loc[i,str(auth_no)+'_author_affs_consolidated_'+str(aff)])


0
Full  
Auth 0 0 
1
Full  
Auth 0 0 
2
Full  
Auth 0 0 
3
Full  Bell Laboratories
Auth 0 0 Bell Laboratories
3
Full  
Auth 1 0 
4
Full  
Auth 0 0 
5
Full  
Auth 0 0 
5
Full  
Auth 1 0 
6
Full  
Auth 0 0 
6
Full  
Auth 1 0 
7
Full  
Auth 0 0 
8
Full  Harvard University
Auth 0 0 Harvard University
9
Full  York University
Auth 0 0 York University
10
Full  
Auth 0 0 
10
Full  
Auth 1 0 
11
Full  
Auth 0 0 
12
Full  
Auth 0 0 
12
Full  
Auth 1 0 
12
Full  
Auth 2 0 
13
Full  Columbia University
Auth 0 0 Columbia University
14
Full  
Auth 0 0 
14
Full  
Auth 1 0 
15
Full  Àarhus Universitet, Denmark, And University Of Essex, United
Auth 0 0 Àarhus Universitet, Denmark
Auth 0 1 University Of Essex, United
16
Full  
Auth 0 0 
16
Full  
Auth 1 0 
16
Full  
Auth 2 0 
17
Full  Harvard University
Auth 0 0 Harvard University
17
Full  California Institute Of Technology
Auth 1 0 California Institute Of Technology
17
Full  University Of Arizona
Auth 2 0 University Of Arizona
18
Full  University of Ca

KeyboardInterrupt: 

In [88]:
print(testdata.columns.values)

['Journal_Name' 'Authors_count' 'Authors_list' 'Article_ID' 'content_type'
 'stable_url' 'Ref_type' 'year' 'ref_string_found'
 'ref_string_found_clean' 'ref_string_raw' 'ref_string_found_clean'
 'ref_string_raw_clean' '0_author_affs' '1_author_affs' '2_author_affs'
 '3_author_affs' '4_author_affs' '0_author_affs_consolidated'
 '1_author_affs_consolidated' '2_author_affs_consolidated'
 '3_author_affs_consolidated' '4_author_affs_consolidated'
 '5_author_affs_consolidated' '5_author_affs'
 '0_author_affs_consolidated_0' '1_author_affs_consolidated_0'
 '2_author_affs_consolidated_0' '0_author_affs_consolidated_1'
 '3_author_affs_consolidated_0' '4_author_affs_consolidated_0'
 '2_author_affs_consolidated_1' '1_author_affs_consolidated_1'
 '1_author_affs_consolidated_2' '0_author_affs_consolidated_2'
 '3_author_affs_consolidated_1']


In [91]:
testdata = testdata[['Journal_Name' ,'Authors_count', 'Authors_list', 'Article_ID', 'content_type',
'stable_url', 'Ref_type' , 'year',
'ref_string_raw' ,
'ref_string_raw_clean',
'ref_string_found',
'ref_string_found_clean' ,
 '0_author_affs', 
 '0_author_affs_consolidated',
 '0_author_affs_consolidated_0',
 '0_author_affs_consolidated_1', 
 '0_author_affs_consolidated_2', 
 '1_author_affs', 
 '1_author_affs_consolidated',
 '1_author_affs_consolidated_0',
 '1_author_affs_consolidated_1',
 '1_author_affs_consolidated_2',
 '2_author_affs',
 '2_author_affs_consolidated',
 '2_author_affs_consolidated_0',
 '2_author_affs_consolidated_1', 
 '3_author_affs',
 '3_author_affs_consolidated', 
 '3_author_affs_consolidated_0',
 '3_author_affs_consolidated_1',
 '4_author_affs',
 '4_author_affs_consolidated',
 '4_author_affs_consolidated_0',
 '5_author_affs', 
 '5_author_affs_consolidated']]

In [92]:
# Excel output to get an overview of the data
testdata.head
testdata.to_excel('/Users/MattJohnson/Desktop/Affiliations/2_Extracting affilitations/3_consolidation/QJE/QJE_aff_ref_output_1940_2010_affs_out authors.xlsx') 